<a href="https://colab.research.google.com/github/kprageet/Car_Detection_System/blob/master/Copy_of_nmit_project_with_textsummarise_final.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

 ### Values for variable which has to be manualy assigned for each pdf
 `pdf_file_path` = name of the pdf
 <br><br> `pages`=  contains all the page numbers for the table of contents present in the pdf 
 <br> Note: the 0th index of the `pages` variable refers to first page, so if table of contents starts from page 3 and<br> ends at page 5, the pages list must start with value 2 i.e.,
 <br> `pages=[2,3,4]`
 <br> <br>`header`= header value of the pdf which is of the format ( `7831 4077–010`)
 

## PDFs used are uploaded in drive
<br>
Variables used for storing the information-<br><br>
 `title` is a list which contains information like - ['Section 1. UCS Application Programming Overview',
 'Section 2. Compiling UCS Programs']<br>
 
 `titles` is a list which contains information in the format- ['UCS Application Programming Overview',
 'Compiling UCS Programs']<br>
 
 `title_index` is a list which contains the title index - ['1', '2', '3', '4', '5', '6', '7', '8']<br>

 `page_num` is a list which contains all the page numbers of every title and subtitle -
 ['1–1',
 '1–1',
 '1–4',
 '1–7',
 '1–11',
 '1–12',
 '1–14',
 '1–15']<br>
 
 
 `indexx` is a list which contains the index number of every subtitle heading -
 ['1.1',
 '1.2',
 '1.3',
 '1.4',
 '1.4.1',
 '1.4.2',
 '1.4.2.1']<br>
 
 `subtitle_heading` is a list which contains all the subtitle heading names-
 ['Document Updates',
 'About This Guide',
 'Extended Mode',
 'Compiling UCS Programs',
 'Compilation Output in the Object Module',
 'Linking UCS Programs with the Linking System']<br>
 
 
 `heading` is a dictionary where the keys = titles, values= list of the title's subtitles-
<br>
{'UCS Application Programming Overview': ['Document Updates',
  'About This Guide',
  'Extended Mode',
  'Compiling UCS Programs',
  'Compilation Output in the Object Module',
  'UCS Application Development Summary',
  'Developing User Applications',
  'Benefits of Extended Mode Hardware and Software'],<br>
 'Compiling UCS Programs': ['Specifying Compiler Options',
  'Letter Options',
  'Keyword Options',
  'Sign-Off Line']}

# Manually updating neccesary information for each pdf
`pdf_file_path` = The Name of the PDF
<br>
`header` = header value of the PDF which is of the format - (8225 2446–000)
<br> `page_start`=the start page number of the table of contents 
<br> `page_end` = the end page number of table of contents

In [ ]:
#eg:  pdf_file_path= "unisys31.pdf" ,header="8225 2446–000" ,page_start=2 , page_end=7
from google.colab import drive
drive.mount('/content/drive/')
%cd /content/drive/My Drive/Unisys OS 2200 Pdfs
pdf_file_path="unisys2.pdf"
header="7862 6744–001"
page_start=2
page_end=12

Drive already mounted at /content/drive/; to attempt to forcibly remount, call drive.mount("/content/drive/", force_remount=True).
/content/drive/My Drive/Unisys OS 2200 Pdfs


### Importing necessary libraries

In [ ]:
import sys
!{sys.executable} -m pip install tika 
!{sys.executable} -m pip install numpy 
!{sys.executable} -m pip install PyPDF2
!{sys.executable} -m pip install PyMuPDF
!pip install -U spacy
!python -m spacy download en_core_web_sm
import nltk
nltk.download('stopwords')
from nltk.corpus import stopwords
stop = set(stopwords.words('english'))
import spacy
import spacy.lang.en.stop_words as STOP_WORDS
from string import punctuation
from heapq import nlargest
punctuation=punctuation+'\n'

### Extracting the table of contents from the pdf 
<br>The pdf name is given in the `pdf_file_path` variable and the page numbers which contains the table of contents must be assigned to the `pages` variable
<br><br>
Result= A pdf is created which contains only the table of contents 
If the pdf name is `info.pdf` , the resulting pdf will be stored as `info_subset.pdf`

### Using tika to read the data from the resulting pdf obtained from the previous step
<br>`raw_data_str` is the variable which contains the content of the resulting pdf i,e., it contains the table of contents information which is extracted from the pdf

In [ ]:
pages=[]
for i in range(page_start,page_end+1):
    pages.append(i)
pages

[2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12]

In [ ]:
#extracting toc from test pdf and storing it in test_subset.pdf
from PyPDF2 import PdfFileReader, PdfFileWriter
 
#pdf_file_path = 'unisys31.pdf'
file_base_name = pdf_file_path.replace('.pdf', '')
 
pdf = PdfFileReader(pdf_file_path)
 
#pages variable must contain all the page numbers for the table of contents present in the pdf 
#count starts from index 0
# so if table of contents starts from page 3, the pages list must start with value 2
#pages = [2,3,4]
pdfWriter = PdfFileWriter()
 
for page_num in pages:
    pdfWriter.addPage(pdf.getPage(page_num))
 
with open('{0}_subset.pdf'.format(file_base_name), 'wb') as f:
    pdfWriter.write(f)
    f.close()

#the result is stored in {pdf_name}_subset.pdf

In [ ]:
from tika import parser ## importing parser method from tika
raw_data = parser.from_file(file_base_name+"_subset.pdf") ## parsing the pdf as a text document
raw_data_str = raw_data['content'] ## content of the parsed data without metadata
print(raw_data_str)

In [ ]:
type(raw_data_str)

### Since `raw_data_str` is a string , we need to convert it to a list for further extracting the titles and subtitles
<br>`sample` is a list which contains the data of `raw_data_str` by using a splitting condition of a new line (.split('\n'))

In [ ]:
#creating empty list
sample=[]
sample=(raw_data_str.split("\n"))
print(sample)
#getting header value from sample list


### Removing of redundant data from `sample` list
In the sample list values, redundant data like the header value is present which needs to be removed.
<br> The word `Contents` is written on each page and the header value for each pdf is different and needs to be updated for each pdf seperately.
<br> The header value is stored in the `header` variable (For reference, header value is of the form `7831 4077–010`)

In [ ]:
#removing Unwanted heading like headers,page numbers and contents title
#here 7831 0505–011 is the header value
f=0
#header="8225 2446–000"
for i in range(len(sample)):
    if "Contents" in sample[i] and f==0:
        sample[i]=""
        f=1
    if  header in sample[i]:
        sample[i]=""

### The `sample` list contains a few empty or null values in the list which are further removed  

In [ ]:
#removing empty lists present in the sample list
while("" in sample) : 
    sample.remove("") 

In [ ]:
#all the table of contents information is stored in sample list
sample


### Extracting the main titles names of each Section and Appendix from the `sample` list
The title names along with their Section/ Appendix number is stored in the `title` list 
<br><br> After stripping the section or appendix number from each title , only the title names are stored in `titles` list
<br><br><b> Method used for extracting titles is - If the words Section or Appendix are present , then that list value is inserted to the `title` list after stripping out the blank spaces
<br> The title index for each title is stored in the `title_index` list  

In [ ]:
#titles=[]
#extracting main titles
title1=[]
for i in range(len(sample)):
    #if "Section" in sample[i] or ("Appendix" in sample[i] and (".1." not in sample[i])):
    if "Section" in sample[i] and (".1." not in sample[i]):
        title1.append(sample[i])
#storing titles along with section number in another variable 
for i in title1:
    #title.append(i.strip())
    i=i.strip()
#after storing the title names we are getting the index values of the titles
#method for getting the title_index- if the title value is "Section 2. Compiling UCS Programs" , we find the position of "."
#and then store the characters from (0,position) => resulting value= "Section 2",later "section" and "Appendix" is removed
#and the resulting value = "2" which will be appended to the title_index list


In [ ]:
#removing unwanted characters from title
random=[]
title=[]
for i in title1:
    if "..." in i:
        j=title1.index(i)
        random.append(j)
random
for i in range(len(title1)):
    if i not in random:
        title.append(title1[i])
        
title

In [ ]:
#obtaining only title names and removing title index and storing it in 'titles' list
titles=[]
for i in range(len(title)):
    string=title[i]
    k=string.find(".")
    s=string[k+1:]
    titles.append(s.strip())
title_index=[]
for string in title:
    k=string.find(".")
    s=string[:k]
    #s=s.replace("Section","").replace("Appendix","").strip()
    s=s.replace("Section","").strip()
    title_index.append(s)

titles

In [ ]:
title_index

### Extracting the subtitles present under each Section or Appendix 
<br>The subtitle heading after extraction is stored in the `subtitle_heading` list.
<br><br> The index for each subtitle is stored in `indexx` list and the page numbers for them is stored in the `page_num` list respectively.
<br><br> After subtitle extraction, a dictionary called `heading` is created which contains the <b> titles as key </b> and <b>the values is a list of their subheadings</b> respectively.
    <br> For eg, heading = { 'Compiling UCS Programs' : ['Specifying Compiler Options', <br>'Letter Options', <br>'Keyword Options',<br> 'Sign-Off Line']}
<br><br>
<b>Method for extracting the subtitles -
    <br> Intially the `indices` list contains the position of the main titles in the `sample` list. This is done by checking if the words 'Section' or 'Appendix' is present in the `sample` list and their position is then stored in `indices` list.
    <br>Then , we loop through the indices list, for each position value stored in the indices list, the title name is extracted and stored as a key in the `heading` dictionary . for each key, we need to get the subtitles for each key as store is as its value in the dictionary.
        <br> We get the positions of one title and the title preceding it through the `indices` list. Using these positions, we loop through all their intermediate values which contains the respective subheadings. All the subheadings are stored in a string format.
    <br> This string format contains data like the index number, the subtitle name, the page number
    <br>So respective functions are defined, to extract the respective index number , subtitle names and page numbers
    <br>`get_index_pageNum()` function is used to extract the index and page number and and store it in `indexx` and `page_num` lists respectively.
    <br> `get_sub()` function is used for extracting the subtitle names for the string. 
    <br></b>The string format will be of the form:
    <br>"1.2. About This Guide ................................................................................ 1–1 " 
    <br> So, respective string operations are done to strip the unneccessary characters and obtain the required names
    

In [ ]:
'''indices = [i for i, x in enumerate(sample) if "Appendix" in x ]
indices'''


In [ ]:
#extracting subtitles
#first loop through section {title_index} and then extract all the subtitles under it
 #getting index of occurence of the word 'Section' in list
indices = [i for i, x in enumerate(sample) if "Section" in x and "..." not in x or ("Appendix" in sample[i] and (".1." not in sample[i]))] 
d=1
d1 = [i for i, x in enumerate(sample) if "Appendix" in x ]
if (len(d1)==0):
    d=0 
heading={}
indexx=[]
page_num=[]
subtitle_heading=[]
#q stores subheading index value
def get_index_pageNum(s):
    j=s.find(" ")
    f=0
    #index variable stores the subheading index
    indexx.append(s[:j-1])
    index=s[:j-1]
    s=s[j:]
    k=s.find(".")
    subtitle_heading.append(s[:k].strip())
    number=index.count(".") 
    s=s[k:].replace(".","")
    page_num.append(s.strip())
    return index

In [ ]:
def remove(te):
    temp=[]
    for s in te:
        j=s.find(" ")
        s=s[j:]
        k=s.find(".")
        temp.append(s[:k].strip())
    return temp
def rem(i):
    temp=""
    j=i.find(" ")
    i=i[j:]
    k=i.find(".")
    temp=(i[:k].strip())
    return temp

def get_sub(st,index):
    s=" "+index+"."
    te=[]
    end=0
    third_sub_heading={}
    #f=0
    matches_positions = [i for i in range(len(st)) if st.startswith(s, i)] 
    start=matches_positions[0]
    te.append(rem(st[:start].strip()))
    get_index_pageNum(st[:start].strip())
    before_string=st[:start].strip()
    for i in range(len(matches_positions)-1):
        start=matches_positions[i]
        end=matches_positions[i+1]
        index=get_index_pageNum(st[start:end].strip())
        number=index.count(".")
        if number<2:
            before_string=st[start:end].strip()
            te.append(rem(st[start:end].strip().replace("   ","").replace('   ',' ').replace('  ',' ').replace(' - ','-')))
            third_sub_heading={}
        elif number>=2:
            
            if ((rem(before_string))) not in third_sub_heading:
                temp=[]
                temp.append(rem(st[start:end].strip().replace("   ","").replace('   ',' ').replace('  ',' ').replace(' - ','-')))
                third_sub_heading[rem(before_string)]=temp
                if (rem(before_string)) in te:
                    te.remove(rem(before_string))
            else:
                third_sub_heading[rem(before_string)].append(rem(st[start:end].strip().replace("   ","").replace('   ',' ').replace('  ',' ').replace(' - ','-')))
            if third_sub_heading not in te:
                te.append(third_sub_heading)
        #print(st[start:end])
    #te[rem(before_string)].append(third_sub_heading)    
    te.append(rem(st[end:].strip().replace("   ","").replace('   ',' ').replace('  ',' ').replace(' - ','-')))
    get_index_pageNum(st[end:].strip())
    #removing unwanted characters from heading
    #te=remove(te)
    return te


In [ ]:
#Loop from first indice to next to next
#if the section has no subheading we insert null 
k=0
v=0
sub=""
for i in range(len(title_index)): #changed from indices to title_index
    text=""
    t=[]
    
    title_name=titles[k]
   # k=k+1
    if i!=len(indices)-1:
        for j in range(indices[i],indices[i+1]-1):
            text+=sample[j+1]
        #print(text)
        text=text.strip()
        if text=="Contents":
            text=""
        if text!="":
        #extracting subtitles from text variable
            index=title_index[k]
            t=get_sub(text,index)
            heading[title_name]=t
        else:
            text="null"
            heading[title_name]=text
    v=i
    k=k+1

if d==0: #if there is no appendix or glossary in the pdf
    for j in range(indices[v],len(sample)-1):
        text+=sample[j+1]
    text=text.strip()
    if text=="Contents":
        text=""
    if text!="":
    #extracting subtitles from text variable
        index=title_index[len(title_index)-1]
        t=get_sub(text,index)
        heading[title_name]=t
    else:
        text="null"
        heading[title_name]=text
    
heading
#page_num   

### Note: Ignore the range index error and run the remaining cells

In [ ]:
indices

In [ ]:
#It can be noticed that page_num list has unwanted or redundant characters which needs to be removed
#removing unwanted letters from page_num list
def rem_letter(str):
    i=str.rfind(" ")
    s=str[i:]
    return s.strip()

for i in range(len(page_num)):
    #convert string to lowercase and Check if `a_string_lowercase` contains letters
    a_string_lowercase = page_num[i].lower()
    contains_letters = a_string_lowercase.islower()
    if contains_letters:
        page_num[i]=rem_letter(page_num[i])



### Printing all the resulting lists obtained after extracting the table of contents 

In [ ]:
title

In [ ]:
#removing extra spaces from the subtitle_heading list
for i in range(len(subtitle_heading)):
        subtitle_heading[i]=subtitle_heading[i].replace("   ","").replace('   ',' ').replace('  ',' ').replace(' - ','-')
while("" in subtitle_heading) :
    subtitle_heading.remove("")
subtitle_heading

In [ ]:
# removing empty lists
for k,v in heading.items():
    for i in v: #iterating through the subheading list values 
        if type(i) is dict:
            
            for item,values in i.items():
                while("" in values) : 
                    values.remove("")
        else:
            if i=="":
                v.remove(i)
            
heading

In [ ]:
#removing unwanted alphabet characters from indexx list
for i in range(len(indexx)-1):
    if indexx[i].isalpha():
        indexx[i]=""
while("" in indexx) :
    indexx.remove("")
#removing unmwanted elements    
for j in indexx:
    count1=0
    for i in j:
        if(i.isdigit()):
            count1=count1+1
    if count1<2:
        #indexx.remove(indexx.index(j))
        #print(indexx.index(j))
        del indexx[indexx.index(j)]
indexx


In [ ]:
#remove alphabets from page_num
for i in page_num:
  if i.isalpha():
    page_num.remove(i)
  if i.find("–")==-1:
    try:
      page_num.remove(i)
    except ValueError:
      pass
page_num

# PART 2- Paragraph Extraction


## Importing necessary libraries

In [ ]:
import sys
!{sys.executable} -m pip install PyMuPDF
from operator import itemgetter
import json
import fitz

## **Steps :**

1. Using PyMuPDF to identify the paragraphs as text with the most used font in the document, headers as anything larger, and subscripts as anything smaller than the paragraph style.
2. Create a list with HTML style element tags such as `<h1>, <p> and <s0>` for the headers, paragraphs, and subscripts.
3. Combine the text elements with these tags such as `<h1>Introduction to OS2200`. The header and paragraphs in the list are separated by a delimiter `|`.
<br>

### The below functions are used to read the text from the pdf , identify the fonts & styles used and assign the 

### element tag (`<h1>,<p><s1>`) to the titles, subtitles and paragraphs

In [ ]:
def fonts(doc, granularity=False):
    styles = {}
    font_counts = {}

    for page in doc:
        blocks = page.getText("dict")["blocks"]
        for b in blocks:  # iterate through the text blocks
            if b['type'] == 0:  # block contains text
                for l in b["lines"]:  # iterate through the text lines
                    for s in l["spans"]:  # iterate through the text spans
                        if granularity:
                            identifier = "{0}_{1}_{2}_{3}".format(s['size'], s['flags'], s['font'], s['color'])
                            styles[identifier] = {'size': s['size'], 'flags': s['flags'], 'font': s['font'],
                                                  'color': s['color']}
                        else:
                            identifier = "{0}".format(s['size'])
                            styles[identifier] = {'size': s['size'], 'font': s['font']}

                        font_counts[identifier] = font_counts.get(identifier, 0) + 1  # count the fonts usage

    font_counts = sorted(font_counts.items(), key=itemgetter(1), reverse=True)

    if len(font_counts) < 1:
        raise ValueError("Zero discriminating fonts found!")

    return font_counts, styles


In [ ]:
def font_tags(font_counts, styles):
    p_style = styles[font_counts[0][0]]  # get style for most used font by count (paragraph)
    p_size = p_style['size']  # get the paragraph's size

    # sorting the font sizes high to low, so that we can append the right integer to each tag
    font_sizes = []
    for (font_size, count) in font_counts:
        font_sizes.append(float(font_size))
    font_sizes.sort(reverse=True)

    # aggregating the tags for each font size
    idx = 0
    size_tag = {}
    for size in font_sizes:
        idx += 1
        if size == p_size:
            idx = 0
            size_tag[size] = '<p>'
        if size > p_size:
            size_tag[size] = '<h{0}>'.format(idx)
        elif size < p_size:
            size_tag[size] = '<s{0}>'.format(idx)

    return size_tag


In [ ]:
def headers_para(doc, size_tag):
    header_para = []  # list with headers and paragraphs
    first = True  # boolean operator for first header
    previous_s = {}  # previous span

    for page in doc:
        blocks = page.getText("dict")["blocks"]
        for b in blocks:  # iterate through the text blocks
            if b['type'] == 0:  # this block contains text

                # REMEMBER: multiple fonts and sizes are possible IN one block

                block_string = ""  # text found in block
                for l in b["lines"]:  # iterate through the text lines
                    for s in l["spans"]:  # iterate through the text spans
                        if s['text'].strip():  # removing whitespaces:
                            if first:
                                previous_s = s
                                first = False
                                block_string = size_tag[s['size']] + s['text']
                            else:
                                if s['size'] == previous_s['size']:

                                    if block_string and all((c == "|") for c in block_string):
                                        # block_string only contains pipes
                                        block_string = size_tag[s['size']] + s['text']
                                    if block_string == "":
                                        # new block has started, so append size tag
                                        block_string = size_tag[s['size']] + s['text']
                                    else:  # in the same block, so concatenate strings
                                        block_string += " " + s['text']

                                else:
                                    header_para.append(block_string)
                                    block_string = size_tag[s['size']] + s['text']

                                previous_s = s

                    # new block started, indicating with a pipe
                    block_string += "|"

                header_para.append(block_string)

    return header_para

### Parsing the pdf path to the above functions to obtain the extracted text from the pdf 
The extracted text from the pdf is in the form of a list which is stored in the `elements` list variable

In [ ]:
document = pdf_file_path
doc = fitz.open(document)
font_counts, styles = fonts(doc, granularity=False)
size_tag = font_tags(font_counts, styles)
elements = headers_para(doc, size_tag)
for i in range(len(elements)):
    if "|" in elements[i]:
        elements[i]=elements[i].replace("|"," ")
    elements[i]=elements[i].replace("   "," ").replace('   ',' ').replace('  ',' ').replace(' - ','-').replace(header," ")

print(elements)

    

### Method used for getting the subtitle information
<br>For eg: If there are two subtitles , "Document Updates" and "About This Guide" , we find the position of both the subtitles and the content present between both the position is the necessary information required for "Document Updates".
<br>`p=text.find("1.1. Document Updates")
<br>q=text.find("1.2. About This Guide")
<br>print(text[p:q])`<br>
But in our case, the value is in a list so we can't use `.find()` . Instead, we find all the occurrences of the substring in the list and take the position of the last occurrence of the string i.e,
<br><br>`temp = "1.3. Extended Mode"
indices = [i for i, x in enumerate(elements) if temp in x ]
p=indices[len(indices)-1]`
<br><br>
`temp = "1.4. OS 2200"
indices1 = [i for i, x in enumerate(elements) if temp1 in x ]
q=indices1[len(indices1)-1]`
<br><br> The values which is present between index p and q, is the information for the heading in `temp` variable.
 <br>This approach is done in an iterative manner where we loop through the `indexx` list which contains the index value of all the subtitles. Next, we use a `temp` variable which is a string contains the index number and subtitle heading. Another variable called `temp1` variable is used which contains the next subtitle heading name and index number . The position of both these string is found out and the text present in between each subtitle name contains the information which is stored in the `result` variable
<br> A dictionary called `subtitle_info` is created which will contain the <b> subtitle name as the key and the information for each subtitle is present in the value of the key-value pair


In [ ]:
##indices = [i for i, x in enumerate(elements) if "5.2. Using the NPC STATUS Command" in x ]
##indices
#print(elements[407:])

In [ ]:
subtitle_info={}
#removing index number,page number
def remove_page_num(s):
  for i in page_num:
    s=s.replace(str(i),"")
  for i in indexx:
    s=s.replace(str(i),"")
  s=s.replace("<h1>","").replace("<h2>","").replace("<h3>","").replace("<h4>","").replace("<h5>","").replace("<h6>","").replace("<h7>","").replace("<h8>","").replace("<h9>","").replace("<h10>","").replace("<h11>","")
  s=s.replace("<p>","").replace("<s1>","").replace("<s2>","").replace("<s3>","").replace("<s4>","").replace("<s5>","").replace("<s6>","").replace("<s7>","").replace("<s8>","").replace("<s9>","").replace("<s10>","").replace("<s11>","")

  return s
for j in range(0,len(indexx)-1):
    temp=indexx[j]+". "+ subtitle_heading[j]
    #temp format = "1.3. Extended Mode"
    if len(temp)>55:
        temp=temp[:30]
    indices = [i for i, x in enumerate(elements) if temp in x ]
    if len(indices)==0:
        temp=subtitle_heading[j]
        if len(temp)>55:
            temp=temp[:30]
        indices = [i for i, x in enumerate(elements) if temp in x ]
        if len(indices)==0:
            temp=indexx[j]+". "+ subtitle_heading[j]
            temp=temp[:16]
            indices = [i for i, x in enumerate(elements) if temp in x ]
            if len(indices)==0:
                temp=indexx[j]+"."
                
                indices = [i for i, x in enumerate(elements) if temp in x ]
                pr=indices[len(indices)-1]
            else:
                pr=indices[len(indices)-1]
        else:
            pr=indices[len(indices)-1]
        pr=indices[len(indices)-1]
    else:
        pr=indices[len(indices)-1]
    #temp format = "1.3. Extended Mode"
    temp1=indexx[j+1]+". "+ subtitle_heading[j+1]
    
    if len(temp1)>55:
        temp1=temp1[:30]
    indicess = [i for i, x in enumerate(elements) if temp1 in x ]
    
    #print(temp1+" "+str(qr))
    if len(indicess)==0:
        temp1=subtitle_heading[j+1]
        if len(temp1)>55:
            temp1=temp1[:30]
        indicess = [i for i, x in enumerate(elements) if temp1 in x ]
        
        
        if len(indicess)==0:
            temp1=indexx[j+1]+". "+ subtitle_heading[j+1]
            temp1=temp1[:16]
            
            indicess = [i for i, x in enumerate(elements) if temp1 in x ]
            #print(indicess)
            if len(indicess)==0:
                temp1=indexx[j+1]+"."
                indicess = [i for i, x in enumerate(elements) if temp1 in x ]
                
                qr=indicess[len(indicess)-1]
            else:
                qr=indicess[len(indicess)-1]
        else:
            qr=indicess[len(indicess)-1]
    else:
        qr=indicess[len(indicess)-1]
    result=""
    for i in range(len(elements)):
        if i>=pr and i<qr:
            result=result+elements[i]
    result=remove_page_num(result)
    subtitle_info.update( {subtitle_heading[j] : result} )
#print(subtitle_heading[j])
#for last element
tempp=indexx[j+1]+". "+ subtitle_heading[j+1]
indicess1 = [i for i, x in enumerate(elements) if tempp in x ]
qr=indicess[len(indicess)-1]
res=elements[qr:]
indicess2 = [i for i, x in enumerate(elements) if "Appendix" in x or "Glossary" in x or "A–1" in x ]
if len(indicess2)==0:
    end=len(elements)-1
else:
    end=indicess2[len(indicess2)-1]
result=""
for i in range(len(elements)):
        if i>=qr and i<end:
            result=result+elements[i]
result=remove_page_num(result)
subtitle_info.update( {subtitle_heading[j+1] : result} )

In [ ]:
#removing title names from subtitle_info
sub_info={} #temp
for i in range(len(titles)):
  for k,v in subtitle_info.items():
    subtitle_info[k]=v.replace(titles[i],"")


In [ ]:
#removing the first subtitle name from the information
for k,v in subtitle_info.items():
  i=v.find(k)
  l=len(k)
  subtitle_info[k]=v[i+l+1:]

subtitle_info

{'About This Guide': 'Purpose This guide is a starting point for the applications programmer who is new to the Universal Compiling System (UCS). This guide has the following main purposes: • Introduces UCS. This guide describes the steps involved in developing and executing UCS programs. It identifies and describes the software used for each step. • Describes how to code and create UCS programs. This guide provides specific instructions, guidelines, and examples for writing applications programs for execution in batch and demand, Transaction Processing (TIP), and High-Volume Transaction Processing (HVTIP) environments. Coding examples aid the applications programmer in understanding how to turn a design specification into a working program or transaction. • Describes how to plan for upgrading to UCS. This guide discusses developing new programs in UCS, how UCS and non-UCS programs coexist on a system by sharing Unisys software and files, and how to upgrade non-UCS programs to UCS.  1–2

In [ ]:
#limiting each paragraph in a title to 300 words since the model cannot process long paragraphs
!pip install nltk
import nltk
nltk.download('punkt')
from nltk.tokenize import sent_tokenize, word_tokenize
def summarize(text):
    var=1
    nlp=spacy.load('en_core_web_sm')
    doc=nlp(text)
    tokens=[token.text for token in doc]
    #punctuation=punctuation+'\n'
    word_frequencies={}
    for word in doc:
      if word.text.lower() not in stop:
        if word.text.lower() not in punctuation:
          if word.text not in word_frequencies.keys():
            word_frequencies[word.text]=1
          else:
            word_frequencies[word.text]+=1
    max_frequency=max(word_frequencies.values())
    for word in word_frequencies.keys():
      word_frequencies[word]=word_frequencies[word]/max_frequency
    sentence_tokens=[sent for sent in doc.sents]
    sentence_score={}
    for sent in sentence_tokens:
      for word in sent:
        if word.text.lower() in word_frequencies.keys():
          if sent not in sentence_score.keys():
            sentence_score[sent]=word_frequencies[word.text.lower()]
          else:
            sentence_score[sent]+=word_frequencies[word.text.lower()]
    if len(text)>300:
      var=float(300/len(text))
    select_length=int(len(sentence_tokens)*var)
    summary=nlargest(300,sentence_score,key=sentence_score.get)
    final_summary=[word.text for word in summary]
    #summary=' '.join(final_summary)
    return final_summary
def token(text):
  #t=word_tokenize(text)
  #t=t[:300]
  t=summarize(text)
  res = ' '.join(map(str, t))
  return res

for k,v in subtitle_info.items():
  text=token(v)
  subtitle_info[k]=text
subtitle_info

### A dictionary called `final` which contains all the titles ,subtitles and their respective data/ information is created
The two dictionaries `heading` and `subtitle_info` are merged together into a `final` dictionary.

In [ ]:
final={}

for k,v in heading.items():
    temporary={}
    if type(v) is str:
        final.update({k:"null"})
    else:
        for i in v: #iterating through the subheading list values 
            if type(i) is dict:
                temp1={}
                for item,values in i.items():
                    for j in values:
                        if j in subtitle_info:
                            text=subtitle_info[j]
                            text=text[:text.find("A-1")]
                            temp1.update({ j : text})
                        else:
                            text=" "
                            temp1.update({ j : text})
                            pass
                    temporary.update({item: temp1})
            else:
                if i in subtitle_info:
                    text=subtitle_info[i]
                    text=text[:text.find("A-1")]
                    temporary.update({ i : text})
                else:
                    text=" "
                    temporary.update({ i : text})
                    pass
        final.update({ k : temporary}) 

if subtitle_heading[len(subtitle_heading)-1] in subtitle_info:
    text=final[titles[len(titles)-1]][subtitle_heading[len(subtitle_heading)-1]]
    text=text[:text.find("Appendix")]
    final[titles[len(titles)-1]][subtitle_heading[len(subtitle_heading)-1]]=text
 

In [ ]:
final

## Checking the error rate i.e., the number of subheadings with null values
`c` variable contains the number of null values.
<br><br>Number of total values can be calculated by finding the length of the `subtitle_heading` list.

In [ ]:
import json
c=0
print("Positions of all the null values: ")
for k,v in list(final.items()):
    if type(v) is dict:
        for item,value in list(v.items()):
            if type(value) is str:
                if value=="":
                    print("final['"+k+"']['"+item+"']")
                    del(final[k][item])
                    c=c+1
            else:
                for it,vl in list(value.items()):
                    if vl=="":
                        print("final['"+k+"']['"+item+"']['"+it+"']")
                        del(final[k][item][it])
                        c=c+1
    if type(v) is str:
        if v=="null" or v=="":
            del(final[k])
            c=c+1
print("\nNumber of null values= "+str(c))
print("\nTotal number of topics= "+str(len(subtitle_heading)-1))

## Converting the resulting dictionary stored in `final` variable to the L1,L2,L3 json format
The L1,L2,L3 json format is as follows:
### If there is just L1 and no (L2,L3) for a title then the format is-
`{"L1s":
    [
     {"L1": "title1",
      "paragraphs": [{
                                 "context": "info1"
                  }]
      },
      {"L1": "title2",
      "paragraphs": [{
                                 "context": "info2"
                  }]
      },
     ]
}`
<br>
### If there is  L1 and L2 but no L3 for a title then the format is-
`{"L1s":
    [
     {"L1": "",
      "L2s": [
              {
                  "L2": "",
                  "paragraphs": [{
                                 "context": ""
                  }]
              },
              {
                  "L2": "",
                  "paragraphs": [{
                                 "context": ""
                  }]
              },       
             ]
      }
     ]
 }`
<br>
### If there is  L1 , L2 and L3 for a title then the format is-
`{"L1s":
    [ 
     {"L1": "",
      "L2s": [
              {
                  "L2": "",
                  "paragraphs": [{
                                 "context": ""
                  }]
              },
              {
                  "L2": "",
                  "L3s":[
                         {
                             "L3": "",
                             "paragraphs": [{
                                            "context":  ""
                             }]
                         },
                         {
                             "L3": "Software",
                             "paragraphs": [{
                                            "context":  ""
                             }]
                         },
                  ]
              },       
              ]
         }
     ]
 }`

In [ ]:
dataset = {}
dataset["data"] = []
dataset

In [ ]:
l1=[]
for k,v in final.items():
    
    if type(v) is dict:
        l2=[]
        for item,value in v.items():
            #l2
            
            if type(value) is str:
                t2="L2"
                p2="paragraphs"
                q2={}
                q2[t2]=item
                #print(t[l])
               # h2= [{"context":  "","qas": [{"answers": [],"question": "","id": ""},{"answers": [],"question": "","id": ""}]}]
                h2= [{"context":  "","qas":[]}]
                h2[0]["context"]=value
                q2[p2]=h2
                dataset["data"].append(
                    {
                        "title": item , "paragraphs" : h2
                    }
                )
                l2.append(q2)
            else:
                #for l3 using u dictionary
                l3=[]
                for it,vl in value.items():
                    t3="L3"
                    p3="paragraphs"
                    q3={}
                    #h3= [{"context":  "","qas": [{"answers": [],"question": "","id": ""},{"answers": [],"question": "","id": ""}]}]
                    h3= [{"context":  "","qas":[]}]
                    q3[t3]=it
                    #print(t[l])
                    h3[0]["context"]=vl
                    q3[p3]=h3
                    dataset["data"].append(
                    {
                        "title": it , "paragraphs" : h3
                    }
                )
                    l3.append(q3)
                #print(l3)
                q2={}
                t2="L2"
                p2="L3s"
                q2[t2]=item
                q2[p2]=l3
                l2.append(q2)
        q1={}
        t1="L1"
        p1="L2s"
        q1[t1]=k
        q1[p1]=l2
        l1.append(q1)
    
    if type(v) is str:
        t1="L1"
        p1="paragraphs"
        q1={}
        #h1= [{"context":  "","qas": [{"answers": [],"question": "","id": ""},{"answers": [],"question": "","id": ""}]}]
        h1= [{"context":  "","qas":[]}]
        q1[t1]=k
        #print(t[l])
        h1[0]["context"]=v
        q1[p1]=h1
        dataset["data"].append(
                    {
                        "title": item , "paragraphs" : h2
                    }
                )
        l1.append(q1)            
        
        
final_result={}
final_result["L1s"]=l1
final_result

In [ ]:
dataset

### The final resulting information is stored in a text file
Note- (for reference) If the pdf name is "unisys.pdf" then the information is stored in a text file called "unisys_info.txt"
<br>i.e, file_name + "_info.txt"

In [ ]:
#final_result is the dictionary where the info is stored 
import json
#pdf_file_path contains the file name which was given at the start
file_base_name = pdf_file_path.replace('.pdf', '')
text_file_name=file_base_name+"_info"+".json" #changed from txt to json
%cd /content/drive/MyDrive/Json_Layered_Format
with open(text_file_name, 'w') as file:
     file.write(json.dumps(final_result))

In [ ]:
#pdf_file_path contains the file name which was given at the start
file_base_name = pdf_file_path.replace('.pdf', '')
text_file_name=file_base_name+"_dset"+".json" #changed from txt to json
%cd /content/drive/My Drive/Json Squad Format/
with open(text_file_name,'w') as file:
     file.write(json.dumps(dataset))

In [ ]:
v1=1
print(v1)
v1=int(300/595)
print(v1)
x1=int(595*v1)
print(x1)

1
0
0
